# Graph rag with predefined node and relationship

Here we use langchain and gemini-1.5-flash llm model to transform the our csv data into graph data then upload them on neo4j auradb.
At time of transformation of data we define the allowed node and relationship.

The credential of neo4j auradb are given below you may login and use them and the graph data also save in pkl file format.

you may see the graph data in drive: [graph_data](https://drive.google.com/drive/folders/1RjNiiFiSBbGLcPtW1_Eaq_x8W7nvINr8?usp=sharing)

In [2]:
%pip install --upgrade --quiet  langchain langchain-community langchain-openai langchain-experimental neo4j tiktoken yfiles_jupyter_graphs
!pip install langchain_groq
!pip install python-dotenv



Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [79]:
!pip install tiktoken

In [1]:
import os
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import DirectoryLoader , TextLoader,CSVLoader
from langchain_community.graphs import Neo4jGraph
from langchain.text_splitter import TokenTextSplitter


Neo4j Credentials

In [ ]:
NEO4J_URI=""
NEO4J_USERNAME=""
NEO4J_PASSWORD=""


In [3]:
os.environ["NEO4J_URI"] = NEO4J_URI
os.environ["NEO4J_USERNAME"] = NEO4J_USERNAME
os.environ["NEO4J_PASSWORD"] = NEO4J_PASSWORD

In [4]:
# Extract data from the docs

def load_data(file_path):
  loader = DirectoryLoader(
        file_path,
        glob="**/*.csv",  # Adjusted for text files
        loader_cls=CSVLoader,
        loader_kwargs={"encoding": "utf-8"} 
    )
  documents = loader.load()
  return documents

In [5]:

documents = load_data("data")


In [6]:
documents

[Document(metadata={'source': 'demo_data\\clean_disease_components.csv', 'row': 0}, page_content="name: Acanthosis nigricans\nlink: https://www.mayoclinic.org/diseases-conditions/acanthosis-nigricans/symptoms-causes/syc-20368983\nAbout: {'symptoms': 'Skin changes are the only signs of acanthosis nigricans. Youll notice dark, thickened, velvety skin in body folds and creases   typically in your armpits, groin and back of the neck. The skin changes usually appear slowly. The affected skin may also have an odor or itch., Consult your doctor if you notice changes in your skin   especially if the changes appear suddenly. You may have an underlying condition that needs treatment., , ,', 'overview': ', Acanthosis nigricans is a skin condition that causes a dark discoloration in body folds and creases. It typically affects the armpits, groin and neck., , Acanthosis nigricans is a skin condition characterized by areas of dark, velvety discoloration in body folds and creases. The affected skin c

In [7]:
#  create text chunks

def create_text_chunks(documents):
    text_splitter = TokenTextSplitter(
        chunk_size = 10000,
        chunk_overlap = 20,
        length_function = len,
        keep_separator=True,
        add_start_index=True,
        strip_whitespace=True,
    )
    chunks = text_splitter.split_documents(documents)
    return chunks


In [8]:
text_chunks = create_text_chunks(documents)
print(len(text_chunks))

1183


In [9]:
for i in range(0,99):
    print(text_chunks[i].page_content)
    print("-------------------------------------")

name: Acanthosis nigricans
link: https://www.mayoclinic.org/diseases-conditions/acanthosis-nigricans/symptoms-causes/syc-20368983
About: {'symptoms': 'Skin changes are the only signs of acanthosis nigricans. Youll notice dark, thickened, velvety skin in body folds and creases   typically in your armpits, groin and back of the neck. The skin changes usually appear slowly. The affected skin may also have an odor or itch., Consult your doctor if you notice changes in your skin   especially if the changes appear suddenly. You may have an underlying condition that needs treatment., , ,', 'overview': ', Acanthosis nigricans is a skin condition that causes a dark discoloration in body folds and creases. It typically affects the armpits, groin and neck., , Acanthosis nigricans is a skin condition characterized by areas of dark, velvety discoloration in body folds and creases. The affected skin can become thick ened. Most often, acanthosis nigricans affects your armpits, groin and neck., The sk

In [4]:
import os
from dotenv import load_dotenv
load_dotenv()

# from langchain_groq import ChatGroq
# os.environ["GROQ_API_KEY"] = os.getenv('GROQ_API_KEY')
# def load_model():
#     llm = ChatGroq(
#         model="llama3-70b-8192",
#         temperature=0
#     )
#     return llm

# Define the Genai model 
from langchain_google_genai import GoogleGenerativeAI
def load_model():
    os.environ["GOOGLE_API_KEY"] = os.getenv('GOOGLE_API_KEY')
    llm  = GoogleGenerativeAI(model="gemini-1.5-flash-latest", temperature=0)
    return llm

In [5]:
llm = load_model()

In [12]:
llm.invoke("What is the capital of France")

'The capital of France is **Paris**. \n'

Function to transform the data into graphdata

In [13]:
from langchain_experimental.graph_transformers import LLMGraphTransformer
llm_transformer = LLMGraphTransformer(
    llm=llm,
    allowed_nodes=[
        "Disease",
        "Symptom",
        "Cause",
        "RiskFactor",
        "Diagnosis",
        "Doctor",
        "Treatment",
        "Medication",
        "MedicalTest"
    ],
    allowed_relationships=[
        "HAS_SYMPTOM",
        "HAS_CAUSE",
        "HAS_RISK_FACTOR",
        "HAS_DIAGNOSIS",
        "CONSULT_WITH",
        "TREATED_BY",
        "PRESCRIBED",
        "DIAGNOSED_BY"
    ]
)


In [14]:
error_prone_indices = []
error_prone_data = []

In [16]:
import pickle
# Directory where the graph documents will be saved
save_directory = "demo_graph_documents"
error_directory = "demo_error_prone_data"
# Create the directory if it doesn't exist
os.makedirs(save_directory, exist_ok=True)
os.makedirs(error_directory, exist_ok=True)

In [17]:
# sometime the conversion of data give the error so we store that data and indices of the data in pkl file then reload and transform again later

file_path = os.path.join(error_directory, "new_error_prone_indices.pkl")
with open(file_path, 'rb') as file:
    error_prone_indices = pickle.load(file)


with open('demo_error_prone_data/new_error_porne_data.pkl', 'rb') as file:
    error_prone_data = pickle.load(file)

In [21]:
import time
start = 592

In [6]:
# connect with the neo4j db instance.
graph = Neo4jGraph()

ValueError: Cannot resolve address b8323791.databases.neo4j.io:7687

Here each text chunks contains the all details of only one diseases and pass one text chunks at time and store them and also upload on neo4j db

In [5]:
for i in range(605, len(text_chunks)):
    # Record the start time of the iteration
    iteration_start_time = time.time()
    try:
      # Convert documents to graph documents
      graph_documents = llm_transformer.convert_to_graph_documents(text_chunks[i:i+1])
    except:
      print(f"Error occurred at index {i} to {i+1}")
      error_prone_indices.append((i, i+1))
      error_prone_data.append(text_chunks[i:i+1])
      file_path = os.path.join(error_directory, "new_error_prone_indices.pkl")
      with open(file_path, "wb") as f:
          pickle.dump(error_prone_indices, f)
      file_path = os.path.join(error_directory, "new_error_porne_data.pkl")
      with open(file_path,"wb") as f:
          pickle.dump(error_prone_data,f)
      continue
    # Add graph documents to the graph
    try:
        graph.add_graph_documents(
            graph_documents,
            baseEntityLabel=True,
            include_source=True
        )
    except:
        graph = Neo4jGraph()
        graph.add_graph_documents(
            graph_documents,
            baseEntityLabel=True,
            include_source=True
        )

    # Record the end time of the iteration
    iteration_end_time = time.time()

    # Calculate the time taken for this iteration
    iteration_time = iteration_end_time - iteration_start_time

    # Print the time taken and the range of documents processed
    print(f"Added documents {start} in {iteration_time:.2f} seconds")

    # Save the graph documents to a file
    file_path = os.path.join(save_directory, f"demo_graph_documents_{start}_.pkl")
    with open(file_path, "wb") as f:
        pickle.dump(graph_documents, f)
    print(f"Saved graph documents to {file_path}")

    # Update start and end for the next iteration
    start = start + 1

NameError: name 'text_chunks' is not defined

In [25]:
#  Error prone data indicese 
for i in range(0, len(error_prone_indices)):
    ind_start = error_prone_indices[i][0]
    ind_end = error_prone_indices[i][1]
    print(ind_start , ind_end)

6 7
15 16
22 23
54 55
62 63
163 164
267 268
336 337
354 355
501 502
529 530
540 541
549 550
605 606
606 607
607 608
610 611
615 616
635 636
654 655
674 675
675 676
680 681
692 693
721 722
733 734
739 740
757 758
833 834
868 869
875 876
893 894
918 919
920 921
941 942
962 963
993 994
1034 1035
1047 1048
1051 1052
1070 1071


In [26]:
start

1145

In [27]:
new_error_prone_indices = []

In [1]:
# here we retries to convert the error prone data into graph data 
# some of them are transform and some of not

for i in range(0, len(error_prone_indices)):
    ind_start = error_prone_indices[i][0]
    # Record the start time of the iteration
    iteration_start_time = time.time()
    try:
      # Convert documents to graph documents
      graph_documents = llm_transformer.convert_to_graph_documents(text_chunks[ind_start:ind_start+1])
    except:
      print(f"Error occurred at index {ind_start}")
      new_error_prone_indices.append(ind_start)
      file_path = os.path.join(error_directory, "recheck_error_prone_indices.pkl")
      with open(file_path, "wb") as f:
          pickle.dump(new_error_prone_indices, f)
      continue
    # Add graph documents to the graph
    try:
        graph.add_graph_documents(
            graph_documents,
            baseEntityLabel=True,
            include_source=True
        )
    except:
        graph = Neo4jGraph()
        graph.add_graph_documents(
            graph_documents,
            baseEntityLabel=True,
            include_source=True
        )

    # Record the end time of the iteration
    iteration_end_time = time.time()

    # Calculate the time taken for this iteration
    iteration_time = iteration_end_time - iteration_start_time

    # Print the time taken and the range of documents processed
    print(f"Added documents {start} in {iteration_time:.2f} seconds")

    # Save the graph documents to a file
    file_path = os.path.join(save_directory, f"demo_graph_documents_{start}_.pkl")
    with open(file_path, "wb") as f:
        pickle.dump(graph_documents, f)
    print(f"Saved graph documents to {file_path}")

    # Update start and end for the next iteration
    start = start + 1

NameError: name 'error_prone_indices' is not defined